In [ ]:
# ..... get cell types using Feng et al markers ..... #

In [2]:
library(SingleCellExperiment)
library(MetaMarkers)
library(Seurat)
library(data.table)
library(dplyr)

In [3]:
# load list of orthologs
om = read.delim('mouse_chicken_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('mouse', 'chicken', 'LCA', 'homology_type')
om <- om[om[,1]!='' & om[,2]!='' & om$homology_type=='ortholog_one2one',]
dim(om)
om[1,]

[1] 12287     4

mouse  chicken LCA     homology_type   
6 mt-Nd1 ND1     Amniota ortholog_one2one

In [4]:
# get list of samples
stages = c(rep('stage23', 2), rep(c('stage28', 'stage32'), each = 3))
samples = c('sample3', 'sample10', 'sample5', 'sample10', 'sample11',
           'sample5', 'sample10', 'sample12')

In [5]:
# function to get top 100 markers for each cell type
get_top_markers <- function(markers, ctypes){
    markers$rank = NA
    for(ii in 1:length(ctypes)){
        id = which(markers$cell_type==ctypes[ii])
        markers$rank[id] = 1:length(id)
    }
    return(markers)
}

In [6]:
# load class markers
markers = fread('~/septation/markers/Feng/Feng_minor_celltype_markers_E10.5_E14.5.csv.gz')
markers$gene <- om$chicken[match(markers$gene, om$mouse)]
markers <- markers[!is.na(markers$gene),]
ctypes = unique(markers$cell_type)

# get rank of markers
markers = get_top_markers(markers, ctypes)

# tibble of group, cell_type, gene, rank
top_markers = as_tibble(markers[which(markers$rank<=100),c('group', 'cell_type', 'gene')])
top_markers[1:2,]

group cell_type gene
1 all   atrial_cm MYL1
2 all   atrial_cm MYH7

In [7]:
# get cell type anno
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(id in 1:length(samples)){
    
    # load seurat object
    sce = readRDS(paste0(stages[id], '_', samples[id], '_data.rds'))

    # get SCE object
    sc3 = SingleCellExperiment(list(counts = sce@assays$RNA@counts))
    colData(sc3) <- DataFrame(sce@meta.data)
    assay(sc3, "cpm") = convert_to_cpm(assay(sc3))
    
    # predict cell type neighborhood
    ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
    ct_enrichment = compute_marker_enrichment(ct_scores)
    ct_pred = assign_cells(ct_scores)
    
    # save
    write.table(ct_pred, file = paste0('annotations/', stages[id], '_', samples[id], '_Feng_celltypes.csv'),
            sep = ',', row.names = T, col.names = T, quote = F)
    
    setTxtProgressBar(pb, id)
}